In [267]:
from numpy import *
from numpy import pi as π
import matplotlib.pyplot as plt

import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from ipywidgets import interactive

In [268]:
def Rx(a):
    """ Rotation matrix around the x-axis by an angle a (in radians). """
    return array([
        [1, 0, 0],
        [0, cos(a), -sin(a)],
        [0, sin(a), cos(a)]
    ])

def Ry(b):
    """ Rotation matrix around the y-axis by an angle b (in radians). """
    return array([
        [cos(b), 0, sin(b)],
        [0, 1, 0],
        [-sin(b), 0, cos(b)]
    ])

def Rz(c):
    """ Rotation matrix around the z-axis by an angle c (in radians). """
    return array([
        [cos(c), -sin(c), 0],
        [sin(c), cos(c), 0],
        [0, 0, 1]
    ])

def Rtot(a, b, c):
    """ Combine rotations around the x, y, and z axes. """
    return dot(Rz(c), dot(Ry(b), Rx(a)))

def rot2d(a, b, ang):
    """ Rotation of points on the xy plane around the z-axis """
    return (
        Rz(ang) @ vstack([a.flatten(), b.flatten(), zeros_like(a.flatten())])
    ).reshape((3, *a.shape))[:2, :, :]

In [ ]:
class GaussianBeam:
    """
    This class is used to represent a General Astigmatic Gaussian Beam.
    """
    def __init__(self,P=1.,λ=1064e-9,q10=66e-3j,q20=-500e-3 + 266e-3j,θ=(20. + 10.j)*π/180.):
        self.P = P
        self.λ = λ
        self.q1 = lambda z: z + q10.real + 1.j*q10.imag
        self.q2 = lambda z: z + q20.real + 1.j*q20.imag
        self.θ = θ

        self.k = 2.*π/λ
        self.Q = lambda z: array([
            [(cos(θ)**2.)/self.q1(z) + (sin(θ)**2.)/self.q2(z),      0.5*sin(2.*θ)*(1./self.q1(z) - 1./self.q2(z))],
            [0.5*sin(2.*θ)*(1./self.q1(z - 1./self.q2(z))),      (sin(θ)**2.)/self.q1(z) + (cos(θ)**2.)/self.q2(z)]
        ],complex128)
        self.E0 = lambda z: sqrt(P/λ*sqrt(
            4.*self.Q(z)[1,1].imag)*self.Q(z)[2,2].imag - (self.Q(z)[1,2] + self.Q(z)[2,1])**2.
        )
        self.η = lambda z: 0.5*(atan(self.q1(z).real/self.q1(z).imag) + atan(self.q2(z).real/self.q2(z).imag))
        self.E = lambda r,z: self.E0(z)*exp(1.j*self.η(z) - 1.j*(self.k/2.)*(r.T @ self.Q(z) @ r))
    
    def simple_astigmatic(self, P=1., λ=700e-9, θx=6.*π/180., θy=12.*π/180.):
        """
        This function is used to redefine the beam as simple astigmatic using the divergence in the x and y directions.
        """
        w0x = λ / (π * θx)
        w0y = λ / (π * θy)

        z0x = (π * (w0x ** 2.)) / λ
        z0y = (π * (w0y ** 2.)) / λ

        q0x = 1.j * z0x
        q0y = 1.j * z0y

        self.__init__(P, λ, q0x, q0y, 0.)

    @staticmethod
    def get_q_parameters_from_Q(Q):
        """
        This static method is used to get the q-parameters and the complex angle θ of a beam given its complex radius
          of curvature tensor Q.
        """
        q1, q2 = linalg.eigvals(Q)
        θ = 0.5*atan((Q[1,2] + Q[2,1]) / (Q[1,1] - Q[2,2]))

        return q1, q2, θ

    def get_elipses_parameters(self,z):
        """
        This function is used to calculate the real parameters needed for intensity and phase ellipses to be drawn
        """

        α = self.θ.real
        β = self.θ.imag
        
        ρ1 = self.q1(z).real/(abs(self.q1(z))**2.)
        ρ2 = self.q2(z).real/(abs(self.q2(z))**2.)

        ω1 = self.q1(z).imag/(abs(self.q1(z))**2.)
        ω2 = self.q2(z).imag/(abs(self.q2(z))**2.)

        return α, β, ρ1, ρ2, ω1, ω2
    
    def intensity_ellipse(self, z):
        """
        This function returns the semi axis and rotation of the intensity elipse.
            
        The intensity elipse (defined by φ_w, w1 and w2 - the angle of rotation and semi-axis) is drawn on the
        plane paralel to xy and containing the informed z point on the axis z, and define the waist shape on the
        corresponding z point.
        """

        α, β, ρ1, ρ2, ω1, ω2 = self.get_elipses_parameters(z)

        φ_w0 = 0.5*arctan2(-(ρ1 - ρ2)*tanh(2.*β),(ω1 - ω2))
        φ_w = unwrap(φ_w0 + α, period=π)

        w1 = 1./sqrt((self.k/4.)*(ω1 + ω2 + sqrt(((ω1 - ω2)**2.)*(cosh(2*β)**2.) + ((ρ1 - ρ2)**2.)*(sinh(2*β)**2.))))
        w2 = 1./sqrt((self.k/4.)*(ω1 + ω2 - sqrt(((ω1 - ω2)**2.)*(cosh(2*β)**2.) + ((ρ1 - ρ2)**2.)*(sinh(2*β)**2.))))

        return φ_w, w1, w2
        
    def phase_ellipse(self, z):
        """
        This function returns the semi axis and rotation of the phase elipse.

        The phase elipse is the elipsoid of curvature matrix:
        C = [[1/R1, 0],[0, 1/R2]]
        on its own coordinate system located at the informed z, with local z equal to global z but axis x and y
        rotated by φ_R around z. This elipsoide is tangent to the point z with concavity directed to the origin of
        the global axis.
        """

        α, β, ρ1, ρ2, ω1, ω2 = self.get_elipses_parameters(z)

        φ_R0 = 0.5*arctan2( (ω1 - ω2)*tanh(2.*β),(ρ1 - ρ2))
        φ_R = unwrap(φ_R0 + α, period=π)

        R1 = 2./(ρ1 + ρ2 + sqrt(((ρ1 - ρ2)**2.)*(cosh(2*β)**2.) + ((ω1 - ω2)**2.)*(sinh(2*β)**2.)))
        R2 = 2./(ρ1 + ρ2 - sqrt(((ρ1 - ρ2)**2.)*(cosh(2*β)**2.) + ((ω1 - ω2)**2.)*(sinh(2*β)**2.)))

        return φ_R, R1, R2
    
    def wavefront_surfaces(self, z, n_points=50):
        """
        This function uses the intensity and phase elipses to calculate wavefronts within the beam waist as
        surfaces with the curvature given by the phase ellipse data and waist given by the intensity elipse data.
        """
        φ_w, w1, w2 = self.intensity_ellipse(z)
        φ_R, R1, R2 = self.phase_ellipse(z)

        θ = linspace(0., 2*π, n_points)
        ρ = linspace(0., 1., n_points)

        Θ, P = meshgrid(θ, ρ)

        surfaces = []
        for zi, w1i, w2i, φ_wi, R1i, R2i, φ_Ri in zip(z, w1, w2, φ_w, R1, R2, φ_R):
            Xw = w1i * P * cos(Θ)
            Yw = w2i * P * sin(Θ)

            X, Y = rot2d(Xw, Yw, φ_wi)

            XR, YR = rot2d(X, Y, -φ_Ri)
            Z = zi - (0.5 * (XR ** 2.) / R1i + 0.5 * (YR ** 2.) / R2i)

            surfaces.append([X,Y,Z])

        return surfaces


In [270]:
import plotly.graph_objects as go

def plot_wavefronts(fig, surfaces):
    for surface in surfaces:
        X,Y,Z = surface
        
        fig.add_trace(go.Surface(
            x=X,
            y=Y,
            z=Z,
            opacity=0.5,
            showscale=False,
            colorscale='reds',
            showlegend=False,
            hoverinfo='none'
        ))

    fig.update_layout(
        title="Visualização 3D da Cintura e Elipsoide de Curvatura",
        scene=dict(
            xaxis=dict(title='X (m)'),
            yaxis=dict(title='Y (m)'),
            zaxis=dict(title='Z (m)'),
        ),
        autosize=False,
        width=800,
        height=600
    )

In [ ]:
gb_ga = GaussianBeam()

z_ga = linspace(-1,1,30)
surfaces_ga = gb_ga.wavefront_surfaces(z_ga)

fig_ga = go.Figure()

plot_wavefronts(fig_ga, surfaces_ga)

fig_ga.show()

In [280]:
gb_sa = GaussianBeam()
gb_sa.simple_astigmatic()

z_sa = linspace(-1e-3, 1e-3, 30)
surfaces_sa = gb_sa.wavefront_surfaces(z_sa)

fig_sa = go.Figure()

plot_wavefronts(fig_sa, surfaces_sa)

fig_sa.update_layout(
    scene=dict(
        xaxis=dict(range=[-0.25e-3,0.25e-3]),
        yaxis=dict(range=[-0.25e-3,0.25e-3]),
    )
)

fig_sa.show()